In [1]:
import pandas as pd
import numpy as np
import plotly.express as px

In [2]:
entitiesEmb = pd.read_csv("entitiesWithEmbeddings.csv", sep="\t", index_col=0)
def convEmbToNumpy(row):
    return np.fromstring(row["embedding"].strip("[ ").strip(" ]"), sep=" ")
entitiesEmb["embedding"] = entitiesEmb.apply(convEmbToNumpy, axis=1)

In [3]:
entitiesEmb.head()

entity      type  idx  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  Provider    0   
1  7180b7e5-d65f-44d5-a031-9853bdf00d83     Visit    1   
2  726e0594-9e72-4b95-87ed-27b34171e2fc   Patient    2   
3  18b64014-1332-4c4d-a680-3965701cc260     Visit    3   
4  ebc3f5c4-6700-34af-8323-85621c313726  Provider    4   

                                           embedding      pca0      pca1  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340... -0.031451 -0.052643   
1  [-0.154994994, 0.0960587263, 0.00670152763, -0...  0.258110  0.096024   
2  [-0.0978377983, 0.00931430701, 0.132475391, 0....  0.025497  0.029595   
3  [-0.04295413, -0.0628375, 0.10074479, 0.071503...  0.033560 -0.567347   
4  [-0.0479423255, -0.0907164812, -0.0340661816, ...  0.051214 -0.744994   

       pca2  
0  0.037770  
1  0.048056  
2 -0.196592  
3  0.811059  
4  1.040570

In [4]:
eEmbDict = pd.Series(entitiesEmb.embedding.values,index=entitiesEmb.entity).to_dict()

In [5]:
fig = px.scatter_3d(entitiesEmb, x='pca0', y='pca1', z='pca2',
              color='type', size=[2 for i in range(len(entitiesEmb))])

fig.show()

In [6]:
entityRel = pd.read_csv("data/train.tsv", sep="\t", header=None)
entityRel.rename(columns={0:"src", 1:"rel", 2:"dest"}, inplace=True)

In [7]:
entityRel.head()

src           rel  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  providerSeen   
1  726e0594-9e72-4b95-87ed-27b34171e2fc   patientSeen   
2  ebc3f5c4-6700-34af-8323-85621c313726  providerSeen   
3  23834663-ed53-3da9-b330-d6e1ecb8428e  providerSeen   
4  69176529-fd1f-3b3f-abce-a0a3626769eb  providerSeen   

                                   dest  
0  7180b7e5-d65f-44d5-a031-9853bdf00d83  
1  18b64014-1332-4c4d-a680-3965701cc260  
2  7d43a8b3-d2d3-46eb-b975-f8bf84cf2e3c  
3  73dd201f-ec55-4b8a-9507-b7ea97741274  
4  ce546deb-be46-44eb-9219-b0c31c7f5984

In [8]:
relations = pd.read_csv("data/relations.tsv", sep="\t", header=None)
relations.rename(columns={0:"idx", 1:"relationType"}, inplace=True)
relations.head()

idx      relationType
0    0      providerSeen
1    1       patientSeen
2    2  patientCondition
3    3      patientVisit
4    4    hasObservation

In [9]:
relEmb = np.load("ckpts/TransE_l2_Synthea_0/Synthea_TransE_l2_relation.npy")
relations["emb"] = [relEmb[i] for i in relations["idx"]]
relations.head()

idx      relationType                                                emb
0    0      providerSeen  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...
1    1       patientSeen  [0.8066311, -0.8114152, 0.8068853, -0.80142224...
2    2  patientCondition  [0.8090767, 0.8112801, 0.80807257, -0.8049854,...
3    3      patientVisit  [-0.81152266, 0.8090401, 0.80835086, -0.806824...
4    4    hasObservation  [-0.8040489, 0.7973249, 0.78698987, 0.8103503,...

In [10]:
rEmbDict = pd.Series(relations.emb.values,index=relations.relationType).to_dict()

In [11]:
entityRel["srcEmb"] = [eEmbDict[i] for i in entityRel["src"]]
entityRel["destEmb"] = [eEmbDict[i] for i in entityRel["dest"]]
entityRel["relEmb"] = [rEmbDict[i] for i in entityRel["rel"]]

In [12]:
entityRel.head()

src           rel  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  providerSeen   
1  726e0594-9e72-4b95-87ed-27b34171e2fc   patientSeen   
2  ebc3f5c4-6700-34af-8323-85621c313726  providerSeen   
3  23834663-ed53-3da9-b330-d6e1ecb8428e  providerSeen   
4  69176529-fd1f-3b3f-abce-a0a3626769eb  providerSeen   

                                   dest  \
0  7180b7e5-d65f-44d5-a031-9853bdf00d83   
1  18b64014-1332-4c4d-a680-3965701cc260   
2  7d43a8b3-d2d3-46eb-b975-f8bf84cf2e3c   
3  73dd201f-ec55-4b8a-9507-b7ea97741274   
4  ce546deb-be46-44eb-9219-b0c31c7f5984   

                                              srcEmb  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340...   
1  [-0.0978377983, 0.00931430701, 0.132475391, 0....   
2  [-0.0479423255, -0.0907164812, -0.0340661816, ...   
3  [-0.0141508, -0.03949995, -0.1527789, -0.12635...   
4  [-0.0763516575, 0.0117169181, 0.04157966, -0.0...   

                                             destEmb  \
0  [-0.154994994, 0.0960587263, 0.00670152763, -0...   
1  [-0.04295413, -0.0628375, 0.10074479, 0.071503...   
2  [-0.03601538, -0.04913606, 0.01070482, 0.02281...   
3  [0.17068535, -0.1616961, 0.24893045, -0.154177...   
4  [-0.10649527, 0.12395856, 0.04711326, -0.08074...   

                                              relEmb  
0  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...  
1  [0.8066311, -0.8114152, 0.8068853, -0.80142224...  
2  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...  
3  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...  
4  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...

In [13]:
entityRel["predSrc"] = entityRel["destEmb"] - entityRel["relEmb"]

In [14]:
entityRel.head()

src           rel  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  providerSeen   
1  726e0594-9e72-4b95-87ed-27b34171e2fc   patientSeen   
2  ebc3f5c4-6700-34af-8323-85621c313726  providerSeen   
3  23834663-ed53-3da9-b330-d6e1ecb8428e  providerSeen   
4  69176529-fd1f-3b3f-abce-a0a3626769eb  providerSeen   

                                   dest  \
0  7180b7e5-d65f-44d5-a031-9853bdf00d83   
1  18b64014-1332-4c4d-a680-3965701cc260   
2  7d43a8b3-d2d3-46eb-b975-f8bf84cf2e3c   
3  73dd201f-ec55-4b8a-9507-b7ea97741274   
4  ce546deb-be46-44eb-9219-b0c31c7f5984   

                                              srcEmb  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340...   
1  [-0.0978377983, 0.00931430701, 0.132475391, 0....   
2  [-0.0479423255, -0.0907164812, -0.0340661816, ...   
3  [-0.0141508, -0.03949995, -0.1527789, -0.12635...   
4  [-0.0763516575, 0.0117169181, 0.04157966, -0.0...   

                                             destEmb  \
0  [-0.154994994, 0.0960587263, 0.00670152763, -0...   
1  [-0.04295413, -0.0628375, 0.10074479, 0.071503...   
2  [-0.03601538, -0.04913606, 0.01070482, 0.02281...   
3  [0.17068535, -0.1616961, 0.24893045, -0.154177...   
4  [-0.10649527, 0.12395856, 0.04711326, -0.08074...   

                                              relEmb  \
0  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...   
1  [0.8066311, -0.8114152, 0.8068853, -0.80142224...   
2  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...   
3  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...   
4  [0.8145279, 0.81424326, 0.8149334, -0.8071564,...   

                                             predSrc  
0  [-0.9695229228291931, -0.7181845307457458, -0....  
1  [-0.849585218256836, 0.7485776954650879, -0.70...  
2  [-0.8505433088291932, -0.8633793170457459, -0....  
3  [-0.643842578829193, -0.9759393570457459, -0.5...  
4  [-0.9210231988291931, -0.6902846970457459, -0....

In [15]:
entityRel["rel"].unique()

array(['providerSeen', 'patientSeen', 'patientCondition', 'patientVisit',
       'hasObservation', 'patientMedication', 'patientObservation',
       'hasCarePlan', 'hasMedication', 'patientProcedure', 'hasCondition',
       'hasProcedure', 'hasImmunization', 'zipInState', 'providerVisit',
       'zipInCity', 'zipHasAddress', 'patientLocatedAt', 'residesAt',
       'hasAllergy', 'patientImmunization', 'hasImagingStudy', 'foundAt',
       'worksAt', 'employs', 'organizationLocatedAt', 'cityInState',
       'patientImagingStudy', 'cityHasZip', 'stateHasZip',
       'patientCarePlan', 'patientAllergy', 'stateHasCity',
       'patientLocation', 'organizationAddress', 'addressInZip',
       'patientAddress', 'organizationLocation'], dtype=object)

In [16]:
import numpy as np
from scipy.spatial.distance import cdist, euclidean

def geometric_median(X, eps=1e-5):
    y = np.mean(X, 0)

    while True:
        D = cdist(X, [y])
        nonzeros = (D != 0)[:, 0]

        Dinv = 1 / D[nonzeros]
        Dinvs = np.sum(Dinv)
        W = Dinv / Dinvs
        T = np.sum(W * X[nonzeros], 0)

        num_zeros = len(X) - np.sum(nonzeros)
        if num_zeros == 0:
            y1 = T
        elif num_zeros == len(X):
            return y
        else:
            R = (T - y) * Dinvs
            r = np.linalg.norm(R)
            rinv = 0 if r == 0 else num_zeros/r
            y1 = max(0, 1-rinv)*T + min(1, rinv)*y

        if euclidean(y, y1) < eps:
            return y1

        y = y1

In [17]:
from sklearn.metrics.pairwise import cosine_similarity
def predictEmbedding(row):
    vid = row["entity"]
    X = np.stack(entityRel[entityRel["src"] == vid]["predSrc"].values)
    predEmb = geometric_median(X)
    tgtEmb = row["embedding"]
    return predEmb, cosine_similarity(tgtEmb.reshape(1, -1), predEmb.reshape(1, -1))[0][0]

In [18]:
entitiesEmb.head()

entity      type  idx  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  Provider    0   
1  7180b7e5-d65f-44d5-a031-9853bdf00d83     Visit    1   
2  726e0594-9e72-4b95-87ed-27b34171e2fc   Patient    2   
3  18b64014-1332-4c4d-a680-3965701cc260     Visit    3   
4  ebc3f5c4-6700-34af-8323-85621c313726  Provider    4   

                                           embedding      pca0      pca1  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340... -0.031451 -0.052643   
1  [-0.154994994, 0.0960587263, 0.00670152763, -0...  0.258110  0.096024   
2  [-0.0978377983, 0.00931430701, 0.132475391, 0....  0.025497  0.029595   
3  [-0.04295413, -0.0628375, 0.10074479, 0.071503...  0.033560 -0.567347   
4  [-0.0479423255, -0.0907164812, -0.0340661816, ...  0.051214 -0.744994   

       pca2  
0  0.037770  
1  0.048056  
2 -0.196592  
3  0.811059  
4  1.040570

In [19]:
entitiesEmb.shape

(47583, 7)

In [20]:
predRes = entitiesEmb.apply(predictEmbedding, axis=1)

In [21]:
predRes.head()

0    ([-7.156589855507111e-05, -0.8062477446484854,...
1    ([-0.041935319805111254, -0.2835468460268735, ...
2    ([0.2750010927612724, 0.027558490346478625, -0...
3    ([-0.07457000168345984, -0.3290538554252914, -...
4    ([0.027358347625924716, -0.8017236792280762, -...
dtype: object

In [22]:
entitiesEmb["predEmb"] = [i[0] for i in predRes]
entitiesEmb["simToOriginal"] = [i[1] for i in predRes]

In [23]:
entitiesEmb.head()

entity      type  idx  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  Provider    0   
1  7180b7e5-d65f-44d5-a031-9853bdf00d83     Visit    1   
2  726e0594-9e72-4b95-87ed-27b34171e2fc   Patient    2   
3  18b64014-1332-4c4d-a680-3965701cc260     Visit    3   
4  ebc3f5c4-6700-34af-8323-85621c313726  Provider    4   

                                           embedding      pca0      pca1  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340... -0.031451 -0.052643   
1  [-0.154994994, 0.0960587263, 0.00670152763, -0...  0.258110  0.096024   
2  [-0.0978377983, 0.00931430701, 0.132475391, 0....  0.025497  0.029595   
3  [-0.04295413, -0.0628375, 0.10074479, 0.071503...  0.033560 -0.567347   
4  [-0.0479423255, -0.0907164812, -0.0340661816, ...  0.051214 -0.744994   

       pca2                                            predEmb  simToOriginal  
0  0.037770  [-7.156589855507111e-05, -0.8062477446484854, ...      -0.129639  
1  0.048056  [-0.041935319805111254, -0.2835468460268735, -...      -0.099329  
2 -0.196592  [0.2750010927612724, 0.027558490346478625, -0....      -0.031411  
3  0.811059  [-0.07457000168345984, -0.3290538554252914, -0...       0.002143  
4  1.040570  [0.027358347625924716, -0.8017236792280762, -0...      -0.052958

In [24]:
entitiesEmb["simToOriginal"].values.mean()

-0.0022258045877882734

In [33]:
def predictMeanEmbedding(row):
    vid = row["entity"]
    X = np.stack(entityRel[entityRel["src"] == vid]["predSrc"].values)
    predEmb = X.mean(axis=0)
    return predEmb, cosine_similarity(row["embedding"].reshape(1, -1), predEmb.reshape(1, -1))[0][0]

In [34]:
predRes = entitiesEmb.apply(predictMeanEmbedding, axis=1)

In [35]:
entitiesEmb["predMeanEmb"] = [i[0] for i in predRes]
entitiesEmb["meanSimToOriginal"] = [i[1] for i in predRes]

In [36]:
entitiesEmb.head()

entity      type  idx  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  Provider    0   
1  7180b7e5-d65f-44d5-a031-9853bdf00d83     Visit    1   
2  726e0594-9e72-4b95-87ed-27b34171e2fc   Patient    2   
3  18b64014-1332-4c4d-a680-3965701cc260     Visit    3   
4  ebc3f5c4-6700-34af-8323-85621c313726  Provider    4   

                                           embedding      pca0      pca1  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340... -0.031451 -0.052643   
1  [-0.154994994, 0.0960587263, 0.00670152763, -0...  0.258110  0.096024   
2  [-0.0978377983, 0.00931430701, 0.132475391, 0....  0.025497  0.029595   
3  [-0.04295413, -0.0628375, 0.10074479, 0.071503...  0.033560 -0.567347   
4  [-0.0479423255, -0.0907164812, -0.0340661816, ...  0.051214 -0.744994   

       pca2                                            predEmb  simToOriginal  \
0  0.037770  [-7.156589855507111e-05, -0.8062477446484854, ...      -0.129639   
1  0.048056  [-0.041935319805111254, -0.2835468460268735, -...      -0.099329   
2 -0.196592  [0.2750010927612724, 0.027558490346478625, -0....      -0.031411   
3  0.811059  [-0.07457000168345984, -0.3290538554252914, -0...       0.002143   
4  1.040570  [0.027358347625924716, -0.8017236792280762, -0...      -0.052958   

                                         predMeanEmb  meanSimToOriginal  
0  [-0.0007389209977994556, -0.8055862833189541, ...          -0.129644  
1  [-0.049393923006935125, -0.30490667618953704, ...          -0.096245  
2  [0.25055225174601886, 0.03689485037911179, -0....          -0.027869  
3  [-0.07144200215693514, -0.354667627684537, -0....           0.000319  
4  [0.026494838814859145, -0.7999421886359253, -0...          -0.052993

In [37]:
entitiesEmb["meanSimToOriginal"].values.mean()

-0.002069638718244423

In [38]:
entitiesEmb.shape

(47583, 11)

In [39]:
entitiesEmb.head()

entity      type  idx  \
0  3d10019f-c88e-3de5-9916-6107b9c0263d  Provider    0   
1  7180b7e5-d65f-44d5-a031-9853bdf00d83     Visit    1   
2  726e0594-9e72-4b95-87ed-27b34171e2fc   Patient    2   
3  18b64014-1332-4c4d-a680-3965701cc260     Visit    3   
4  ebc3f5c4-6700-34af-8323-85621c313726  Provider    4   

                                           embedding      pca0      pca1  \
0  [-0.12480221, 0.05798539, 0.10484781, 0.045340... -0.031451 -0.052643   
1  [-0.154994994, 0.0960587263, 0.00670152763, -0...  0.258110  0.096024   
2  [-0.0978377983, 0.00931430701, 0.132475391, 0....  0.025497  0.029595   
3  [-0.04295413, -0.0628375, 0.10074479, 0.071503...  0.033560 -0.567347   
4  [-0.0479423255, -0.0907164812, -0.0340661816, ...  0.051214 -0.744994   

       pca2                                            predEmb  simToOriginal  \
0  0.037770  [-7.156589855507111e-05, -0.8062477446484854, ...      -0.129639   
1  0.048056  [-0.041935319805111254, -0.2835468460268735, -...      -0.099329   
2 -0.196592  [0.2750010927612724, 0.027558490346478625, -0....      -0.031411   
3  0.811059  [-0.07457000168345984, -0.3290538554252914, -0...       0.002143   
4  1.040570  [0.027358347625924716, -0.8017236792280762, -0...      -0.052958   

                                         predMeanEmb  meanSimToOriginal  
0  [-0.0007389209977994556, -0.8055862833189541, ...          -0.129644  
1  [-0.049393923006935125, -0.30490667618953704, ...          -0.096245  
2  [0.25055225174601886, 0.03689485037911179, -0....          -0.027869  
3  [-0.07144200215693514, -0.354667627684537, -0....           0.000319  
4  [0.026494838814859145, -0.7999421886359253, -0...          -0.052993

In [41]:
data = entitiesEmb.loc[(entitiesEmb["embedding"].str.len() != 0)][["entity", "embedding", "predEmb"]]

In [42]:
from sklearn.model_selection  import train_test_split
import torch
import torch.nn.functional as F

In [43]:
X = data["predEmb"]
y = data["embedding"]

In [44]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [45]:
#Define training hyperprameters.
batch_size = 100
num_epochs = 500
learning_rate = 0.01

In [46]:
#Calculate some other hyperparameters based on data.  
batch_no = len(X_train) // batch_size  #batches
cols=len(X_train[0])
n_output=len(y_train[0])

In [52]:
#Create the model
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# Assume that we are on a CUDA machine, then this should print a CUDA device:
print("Executing the model on :",device)
net = torch.nn.Sequential(
    torch.nn.Linear(cols, 1000),
    torch.nn.LeakyReLU(),
    #torch.nn.Dropout(.20),
    torch.nn.Linear(1000,1000),
    torch.nn.LeakyReLU(),
    #torch.nn.Dropout(.20),
    torch.nn.Linear(1000, n_output)
)

Executing the model on : cpu


In [53]:
print(net)

Sequential(
  (0): Linear(in_features=200, out_features=500, bias=True)
  (1): LeakyReLU(negative_slope=0.01)
  (2): Linear(in_features=500, out_features=500, bias=True)
  (3): LeakyReLU(negative_slope=0.01)
  (4): Linear(in_features=500, out_features=200, bias=True)
)


In [54]:
#Adam is a specific flavor of gradient decent which is typically better
optimizer = torch.optim.Adam(net.parameters(), lr=learning_rate)


#optimizer = torch.optim.SGD(net.parameters(), lr=0.2)
criterion = torch.nn.MSELoss(size_average=False)  # this is for regression mean squared loss

cos = torch.nn.CosineSimilarity(dim=0)

In [55]:
#Change to numpy arraay. 
X_train=np.stack(X_train, axis=0)
y_train=np.stack(y_train, axis=0)
X_test=np.stack(X_test, axis=0)
y_test=np.stack(y_test, axis=0)

In [56]:
from sklearn.utils import shuffle
from torch.autograd import Variable
import math

for epoch in range(num_epochs):
    running_loss = 0.0
    avgSim = 0
    #Shuffle just mixes up the dataset between epocs
    X_train, y_train = shuffle(X_train, y_train)
    # Mini batch learning
    for i in range(batch_no):
        start = i * batch_size
        end = start + batch_size
        inputs = Variable(torch.FloatTensor(X_train[start:end]))
        labels = Variable(torch.FloatTensor(y_train[start:end]))
        # zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        #print("outputs",outputs)
        #print("outputs",outputs,outputs.shape,"labels",labels, labels.shape)
        #loss = torch.acos(cos(outputs, torch.unsqueeze(labels,dim=0)[0]))/math.pi
        #loss.mean().backward()
        #print(loss)
        loss = criterion(outputs, torch.unsqueeze(labels,dim=1))
        loss.backward()
        
        optimizer.step()

        for i in range(len(inputs)):
            avgSim += cos(net(Variable(torch.FloatTensor(inputs[i]))), torch.FloatTensor(labels[i]))

        # print statistics
        running_loss += loss.mean().item()

    simAccuracy = (avgSim/len(X_train)).item()
    print('Epoch {}'.format(epoch+1), "loss: ",running_loss, "\taccuracy: ", simAccuracy)

Epoch 1 loss:  1124297019.40625 	accuracy:  0.025516849011182785
Epoch 2 loss:  694013511.9257812 	accuracy:  0.015096256509423256
Epoch 3 loss:  651172869.203125 	accuracy:  0.0217448640614748
Epoch 4 loss:  26561009.640625 	accuracy:  0.03195831552147865
Epoch 5 loss:  23700777.296875 	accuracy:  0.03834179788827896
Epoch 6 loss:  23124360.5859375 	accuracy:  0.04121552035212517
Epoch 7 loss:  23846164.23828125 	accuracy:  0.04117664694786072
Epoch 8 loss:  22821587.9375 	accuracy:  0.042222145944833755
Epoch 9 loss:  22505366.0703125 	accuracy:  0.04494212195277214
Epoch 10 loss:  22471793.1953125 	accuracy:  0.04605080559849739
Epoch 11 loss:  22635530.33203125 	accuracy:  0.044392913579940796
Epoch 12 loss:  23911282.39453125 	accuracy:  0.03852000832557678
Epoch 13 loss:  22517999.6796875 	accuracy:  0.04610862582921982
Epoch 14 loss:  23071428.24609375 	accuracy:  0.044526107609272
Epoch 15 loss:  28989069.625 	accuracy:  0.03310006111860275
Epoch 16 loss:  22305751.828125 	accu

KeyboardInterrupt: 

In [ ]:
avgSim = 0
sims = []
for i in range(len(X_test)):
    sim = cos(net(Variable(torch.FloatTensor(X_test[i]))), torch.FloatTensor(y_test[i])).item()
    avgSim +=sim
    sims.append(sim)

simAccuracy = (avgSim/len(X_test))

print("The average similarity between actual and predicted embeddings is:", simAccuracy)

In [ ]:
import matplotlib.pyplot as plt

%matplotlib inline
x = sims
plt.hist(x, density=False, bins=20)  # `density=False` would make counts
plt.ylabel('Count')
plt.xlabel('Data')

In [ ]:
avgSim = 0
sims = []
for i in range(len(X_train)):
    sim = cos(net(Variable(torch.FloatTensor(X_train[i]))), torch.FloatTensor(y_train[i])).item()
    avgSim +=sim
    sims.append(sim)

simAccuracy = (avgSim/len(X_train))

print("The average similarity between actual and predicted embeddings is:", simAccuracy)

In [ ]:
%matplotlib inline
x = sims
plt.hist(x, density=False, bins=30)  # `density=False` would make counts
plt.ylabel('Count')
plt.xlabel('Data')

In [ ]:
torch.save(net.state_dict(), "./embeddingPrediction.model")